In [1]:
#import tensorflow and force eager execution for gradcam (numpy etc)

import tensorflow as tf
print("TensorFlow version:", tf.__version__)

use_device='/gpu:0'


import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import keras

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Embedding, Conv1D, GlobalMaxPooling1D, Dense, Input, Concatenate, BatchNormalization
from tensorflow.keras.layers import LSTM

from tensorflow.python.client import device_lib

#import models and layers from tensorflow.keras to avoid errors like "TypeError: Checkpointable._track_checkpointable()"
from tensorflow.keras.models import Model
from tensorflow.keras.models import load_model

from tensorflow.keras.layers import Dropout, Activation, Flatten
from keras.optimizers import Adam
    
from tensorflow.keras.preprocessing import image
from tensorflow.keras.preprocessing.image import ImageDataGenerator
    
from keras.utils import layer_utils
from keras.utils.data_utils import get_file
from keras.applications.imagenet_utils import preprocess_input
from IPython.display import SVG
from keras.utils.vis_utils import model_to_dot
from keras.utils import plot_model
#import tensorflow.keras.backend as K
from keras import regularizers
    
import pickle
import pandas as pd

from datetime import datetime

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

    
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\tensorflow\python\framework\dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\tensorflow\python\framework\dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\tensorflow\python\framework\dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([

TensorFlow version: 1.13.1


Using TensorFlow backend.
C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\sklearn\utils\validation.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  LARGE_SPARSE_SUPPORTED = LooseVersion(scipy_version) >= '0.14.0'


[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 12660150378286730514
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 1420715622
locality {
  bus_id: 1
  links {
  }
}
incarnation: 9417153999981102929
physical_device_desc: "device: 0, name: NVIDIA GeForce GTX 1650, pci bus id: 0000:01:00.0, compute capability: 7.5"
]


In [2]:
# define paths and functions for loading models, define names, etc
# ========================================================================================================================   
path_data= "xxx" #where is the dataset
path_data_2= "xxx" #where to store the results (specific path)



def load_model_from_path(model_path):
    """
    Load a Keras model from the specified path.
    Parameters:
        model_path (str): The path to the model file.
    Returns:
        model: The loaded Keras model.
    """
    try:
        MODEL = load_model(model_path)
        print("Model loaded successfully.")
        return MODEL
    except Exception as e:
        print("Error loading model:", e)
        


models_names_act= [
    "LogP_Acts.model",
    "Tg_Acts.model",
    "LogS_Acts.model", "pKa_Acts.model"]

In [3]:
# import chi data for testing
# ========================================================================================================================  

X1_import=path_data + "SMILES_1.txt" #where is the Xdata of the dataset (SMILES)
X2_import=path_data + "SMILES_2.txt"
# Load the saved numeric arrays from the file
Y_import=path_data + "K_GT.txt" #where is the Ydata of the dataset (property to predict)
   

# Load SMILES strings from file
with open(X1_import, 'r') as f:
    smiles_data_1 = f.readlines()
with open(X2_import, 'r') as f:
    smiles_data_2 = f.readlines()

# Load properties from file
with open(Y_import, 'r') as f:
    X_data = f.readlines()
    
print(smiles_data_1[10])
print(smiles_data_2[10])
print(X_data[10])

OC[C@H]1O[C@H](O[C@H]2O[C@H](CO)[C@@H](O)[C@H](O)[C@H]2O)[C@H](O)[C@@H](O)[C@@H]1O

OC[C@H]1O[C@H](O[C@]2(CO)O[C@H](CO)[C@@H](O)[C@@H]2O)[C@H](O)[C@@H](O)[C@@H]1O

0.56



In [4]:
# Convert the dataset into activation arrays with the pre-trained models
# ======================================================================================================================== 

# Load the tokenizer
tokenizer_path = path_data_2 + 'tokenizer_all.pkl'
with open(tokenizer_path, 'rb') as f:
    tokenizer_1 = pickle.load(f)
with open(tokenizer_path, 'rb') as f:
    tokenizer_2 = pickle.load(f) 

# Preprocess SMILES data for SMILES_1
sequences_1 = tokenizer_1.texts_to_sequences(smiles_data_1)
vocab_size_1 = len(tokenizer_1.word_index) + 1
print(f"Vocab size 1: {vocab_size_1}")
# Check the maximum index in sequences
max_index_1 = max(max(seq) for seq in sequences_1 if seq)
print(f"Maximum index in sequence 1: {max_index_1}")

# Preprocess SMILES data for SMILES_2
sequences_2 = tokenizer_2.texts_to_sequences(smiles_data_2)
vocab_size_2 = len(tokenizer_2.word_index) + 1
print(f"Vocab size 2: {vocab_size_2}")
# Check the maximum index in sequences
max_index_2 = max(max(seq) for seq in sequences_2 if seq)
print(f"Maximum index in sequence 2: {max_index_2}")

# Ensure all indices in sequences_1 are within the valid range
for seq in sequences_1:
    for idx in seq:
        if idx >= vocab_size_1:
            print(f"Found out-of-bounds index in sequences_1: {idx}")
# Ensure all indices in sequences_2 are within the valid range
for seq in sequences_2:
    for idx in seq:
        if idx >= vocab_size_2:
            print(f"Found out-of-bounds index in sequences_2: {idx}")

# ---------------------------------------------------------------------------
# Convert property data to numpy array
X_labels = np.array([float(prop.strip()) for prop in X_data])

# Define embedding dimension
embedding_dim = 128

max_len=[168, 105, 84, 88] #remember that each model has a different value

Vocab size 1: 32
Maximum index in sequence 1: 27
Vocab size 2: 32
Maximum index in sequence 2: 19


In [5]:
# Load each model, pass the X dataset, and store the activation arrays
# =======================================================================

acts_dict={}
for i in range(len(models_names_act)):
    model_name=models_names_act[i]
    print(model_name)
    try:
        model_path = path_data_2 + model_name
        model_temp = load_model_from_path(model_path)
        max_length = max_len[i]
        
        # Predict output 1
        padded_sequences_1 = pad_sequences(sequences_1, maxlen=max_length, padding='post')
        print("Padding ok, padding shape: ")
        print(np.shape(padded_sequences_1))
        acts_1 = model_temp.predict(padded_sequences_1)
        print("Predict ok, act shape: ")
        print(np.shape(acts_1))
        # Predict output 2
        padded_sequences_2 = pad_sequences(sequences_2, maxlen=max_length, padding='post')
        print("Padding ok, padding shape: ")
        print(np.shape(padded_sequences_2))
        acts_2 = model_temp.predict(padded_sequences_2)
        print("Predict ok, act shape: ")
        print(np.shape(acts_2))
        
        # Store activation arrays for the model
        acts_dict[model_name + "_acts_1"] = acts_1
        acts_dict[model_name + "_acts_2"] = acts_2
        
    except Exception as e:
        print("Error using model:", e)

LogP_Acts.model
Instructions for updating:
Colocations handled automatically by placer.
Model loaded successfully.
Padding ok, padding shape: 
(40, 168)
Predict ok, act shape: 
(40, 50)
Padding ok, padding shape: 
(40, 168)
Predict ok, act shape: 
(40, 50)
Tg_Acts.model
Model loaded successfully.
Padding ok, padding shape: 
(40, 105)
Predict ok, act shape: 
(40, 50)
Padding ok, padding shape: 
(40, 105)
Predict ok, act shape: 
(40, 50)
LogS_Acts.model
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
Model loaded successfully.
Padding ok, padding shape: 
(40, 84)
Predict ok, act shape: 
(40, 50)
Padding ok, padding shape: 
(40, 84)
Predict ok, act shape: 
(40, 50)
pKa_Acts.model
Model loaded successfully.
Padding ok, padding shape: 
(40, 88)
Predict ok, act shape: 
(40, 50)
Padding ok, padding shape: 
(40, 88)
Predict ok, act shape: 
(40, 50)


In [6]:
# Extract the data
X11 = acts_dict["LogP_Acts.model_acts_1"]
X12 = acts_dict["Tg_Acts.model_acts_1"]
X13 = acts_dict["LogS_Acts.model_acts_1"]
X14 = acts_dict["pKa_Acts.model_acts_1"]

# Extract the data
X21 = acts_dict["LogP_Acts.model_acts_2"]
X22 = acts_dict["Tg_Acts.model_acts_2"]
X23 = acts_dict["LogS_Acts.model_acts_2"]
X24 = acts_dict["pKa_Acts.model_acts_2"]

# Labels
y = X_labels

# Split each set of data into training and test sets
test_size = 0.2
random_state = 42


X11_train, X11_test, y_train, y_test = train_test_split(X11, y, test_size=test_size, random_state=random_state)
X12_train, X12_test = train_test_split(X12, test_size=test_size, random_state=random_state)
X13_train, X13_test = train_test_split(X13, test_size=test_size, random_state=random_state)
X14_train, X14_test = train_test_split(X14, test_size=test_size, random_state=random_state)

X21_train, X21_test = train_test_split(X21, test_size=test_size, random_state=random_state)
X22_train, X22_test = train_test_split(X22, test_size=test_size, random_state=random_state)
X23_train, X23_test = train_test_split(X23, test_size=test_size, random_state=random_state)
X24_train, X24_test = train_test_split(X24, test_size=test_size, random_state=random_state)

X_train_list = [X11_train, X12_train, X13_train, X14_train, X21_train, X22_train, X23_train, X24_train]

print(np.shape(X11_train))
print(np.shape(X21_train))
print(np.shape(X11_test))
print(np.shape(X21_test))

(32, 50)
(32, 50)
(8, 50)
(8, 50)


In [7]:
# Define the test data arrays

X_test_list = [X11_test, X12_test, X13_test, X14_test, 
               X21_test, X22_test, X23_test, X24_test]

# Save each array to a separate .npy file
for idx, array in enumerate(X_test_list):
    np.save(path_data_2 + f'X_test_{idx}.npy', array)
    
# Save y_test to a .npy file
np.save(path_data_2 + 'y_test.npy', y_test)

In [8]:
from keras.callbacks import Callback

  
    
# checkpoint_filepath = path_data_2 + "Weights.npy" #'checkpoint'
monitor_custom='val_mean_absolute_error' #val_mean_absolute_error   val_mean_absolute_percentage_error
mode_custom='min'



early_stop= tf.keras.callbacks.EarlyStopping(monitor=monitor_custom,  verbose=3,
                                             mode=mode_custom, patience=600, restore_best_weights=True)

callback_list= [early_stop]




def Model_combined(X_train_list, y_train, alpha, NeuronsFC, lr, beta_1, beta_2, epsilon, decay, amsgrad, 
                   ep, b_s, v_s, Drop, shuffle_dataset, callback_list):
    """
    Function to create, compile and train a combined model with multiple inputs. Returns the trained Keras model.
    """
    
    # Define the neural network with 10 input branches (first 5 component 1 and the others component 2)
    size_input = 50
    N_models = 4
    input_layers = [Input(shape=(size_input,)) for _ in range(N_models*2)]
    # Normalize each input layer before concatenating
    normalized_inputs = [BatchNormalization()(input_layer) for input_layer in input_layers]
    
    merged_1 = tf.keras.layers.concatenate(normalized_inputs[:N_models])
    merged_2 = tf.keras.layers.concatenate(normalized_inputs[N_models:])
    
    # Define first network
    A = Dense(50)(merged_1)
    A = tf.keras.layers.LeakyReLU(alpha)(A)
    A = Dropout(Drop)(A)
    A = Dense(20)(A)
    A = tf.keras.layers.LeakyReLU(alpha)(A)
    A = Dropout(Drop)(A)
    # Define second network
    A2 = Dense(50)(merged_2)
    A2 = tf.keras.layers.LeakyReLU(alpha)(A2)
    A2 = Dropout(Drop)(A2)
    A2 = Dense(20)(A2)
    A2 = tf.keras.layers.LeakyReLU(alpha)(A2)
    A2 = Dropout(Drop)(A2)
    # Concatenate the outputs of the two networks
    concatenated = tf.keras.layers.concatenate([A, A2])
    merged = Dense(NeuronsFC)(concatenated)
    merged = tf.keras.layers.LeakyReLU(alpha)(merged)
    output_layer = Dense(1, activation='linear')(merged)
    
    # Create model
    MODEL = tf.keras.Model(inputs=input_layers, outputs=output_layer, name="MODEL")
    print(MODEL.summary())
    
    # Compile model
    opt = tf.keras.optimizers.Adam(lr, beta_1, beta_2, epsilon, decay, amsgrad)
    MODEL.compile(loss='mean_absolute_error', optimizer=opt,
                  metrics=['mean_absolute_error', 'mean_absolute_percentage_error'])
    
    # Train the model
    HISTORY = MODEL.fit(X_train_list, y_train, epochs=ep, batch_size=b_s, validation_split=v_s,
              shuffle=shuffle_dataset, callbacks=callback_list)
    
    return MODEL, HISTORY

In [9]:
#DATA=====================================================================================================
Mode=0
#NUMBER OF TEST===========================================================================================
number_of_test = 1
#FREEZE_LAYERS============================================================================================
is_trainable_conv1_1=True #
is_trainable_conv1_2=True #
is_trainable_conv1_3=True #
is_trainable_conv1_4=True #
is_trainable_conv1_5=True
is_trainable_HIDDEN_A1_0=True #the CNN input side of the ANN
is_trainable_HIDDEN_A2_0=True #the Hbonds input side of the ANN (1:True, 2:True, 2:False)
is_trainable_HIDDEN_FC_all=True #concatenated FCs
#HYPERPARAMETERS==========================================================================================
lr=[0.01, 0.001, 0.0001]
beta_1=0.99
beta_2=0.999
epsilon=None
decay=0
amsgrad=True
b_s=[1000, 30, 15, 5, 2]
samples_on_control=0
samples_on_test=200
v_s= 0.2 #(samples_on_test+samples_on_control)/number_of_samples_X   
shuffle_dataset="False"
Drop_prob=0.3
alpha=0.05
reg=0.01
#WORKING PARAMETERS======================================================================================
number_epochs=5000 #
#FULLY CONNECTED=========================================================================================
NeuronsFC=50 # neurons combined FC
NeuronsFC_A2=5 #neurons in the Hbonds input
NeuronsFC_A1=5 #neurons in the CNN input
#CNN=====================================================================================================
w1=1 # must be the same if the model has been pre-trained
w2=6
w3=10
channels_1=32
channels_2=64
channels_3=128

In [10]:
# Iterate over each combination of learning rate and batch size

counter=0
Results=[]
for i in b_s:
    for j in lr:
        Name_saving="KGT_embedding_" + str(counter) + str(number_of_test)
        print("model name (to save): " + Name_saving)
        MODEL, HISTORY= Model_combined(X_train_list, y_train, alpha, NeuronsFC, j, beta_1, beta_2, epsilon, decay, amsgrad, 
                   number_epochs, i, v_s, Drop_prob, shuffle_dataset, callback_list)
        #save model
        try:
            MODEL.save(path_data_2 + Name_saving + ".model")
            print("Model saved")
        except:
            print("Model saved?")
            try:
                MODEL.save(path_data_2 + Name_saving + ".model")
                print("Model now saved!")
            except Exception as e:
                print("Error saving model:", e)
            
        # Extract the mean absolute error from the training history
        mean_absolute_error_model = HISTORY.history['mean_absolute_error'][-1]  # Considering the last epoch error
        val_mean_absolute_error_model = HISTORY.history['val_mean_absolute_error'][-1]
        MAPE_model = HISTORY.history['mean_absolute_percentage_error'][-1]  # Considering the last epoch error
        val_MAPE_model = HISTORY.history['val_mean_absolute_percentage_error'][-1]
        # Append the results to the list
        Results.append([counter, j, i, mean_absolute_error_model, val_mean_absolute_error_model, MAPE_model, val_MAPE_model])            
        counter+=1

model name (to save): KGT_embedding_01
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 50)           0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, 50)           0                                            
__________________________________________________________________________________________________
input_3 (InputLayer)            (None, 50)           0                                            
__________________________________________________________________________________________________
input_4 (InputLayer)            (None, 50)           0                                            
______________________________________________________________________

Epoch 1/5000
25/25 [==============================] - 3s 131ms/sample - loss: 0.4689 - mean_absolute_error: 0.4689 - mean_absolute_percentage_error: 81.1711 - val_loss: 5.5718 - val_mean_absolute_error: 5.5718 - val_mean_absolute_percentage_error: 2023.1093
Epoch 2/5000
25/25 [==============================] - 0s 4ms/sample - loss: 1.1343 - mean_absolute_error: 1.1343 - mean_absolute_percentage_error: 261.2675 - val_loss: 2.8969 - val_mean_absolute_error: 2.8969 - val_mean_absolute_percentage_error: 1050.7262
Epoch 3/5000
25/25 [==============================] - 0s 3ms/sample - loss: 0.7470 - mean_absolute_error: 0.7470 - mean_absolute_percentage_error: 153.0357 - val_loss: 0.7062 - val_mean_absolute_error: 0.7062 - val_mean_absolute_percentage_error: 248.0811
Epoch 4/5000
25/25 [==============================] - 0s 3ms/sample - loss: 1.0769 - mean_absolute_error: 1.0769 - mean_absolute_percentage_error: 254.4288 - val_loss: 0.3060 - val_mean_absolute_error: 0.3060 - val_mean_absolute_

25/25 [==============================] - 0s 2ms/sample - loss: 0.3627 - mean_absolute_error: 0.3627 - mean_absolute_percentage_error: 75.4384 - val_loss: 0.4115 - val_mean_absolute_error: 0.4115 - val_mean_absolute_percentage_error: 86.5205
Epoch 34/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.4216 - mean_absolute_error: 0.4216 - mean_absolute_percentage_error: 94.5431 - val_loss: 0.4033 - val_mean_absolute_error: 0.4033 - val_mean_absolute_percentage_error: 84.0934
Epoch 35/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.5449 - mean_absolute_error: 0.5449 - mean_absolute_percentage_error: 110.1729 - val_loss: 0.3713 - val_mean_absolute_error: 0.3713 - val_mean_absolute_percentage_error: 76.0881
Epoch 36/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.4041 - mean_absolute_error: 0.4041 - mean_absolute_percentage_error: 91.7172 - val_loss: 0.3222 - val_mean_absolute_error: 0.3222 - val_mean_absolute_percentage_error: 6

Epoch 66/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.2734 - mean_absolute_error: 0.2734 - mean_absolute_percentage_error: 50.7540 - val_loss: 0.1572 - val_mean_absolute_error: 0.1572 - val_mean_absolute_percentage_error: 24.3824
Epoch 67/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.2236 - mean_absolute_error: 0.2236 - mean_absolute_percentage_error: 48.5253 - val_loss: 0.1596 - val_mean_absolute_error: 0.1596 - val_mean_absolute_percentage_error: 23.9810
Epoch 68/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.2588 - mean_absolute_error: 0.2588 - mean_absolute_percentage_error: 51.9469 - val_loss: 0.1603 - val_mean_absolute_error: 0.1603 - val_mean_absolute_percentage_error: 23.1480
Epoch 69/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.2009 - mean_absolute_error: 0.2009 - mean_absolute_percentage_error: 42.7394 - val_loss: 0.1684 - val_mean_absolute_error: 0.1684 - val_mean_absolute_percen

Epoch 99/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.1744 - mean_absolute_error: 0.1744 - mean_absolute_percentage_error: 32.9170 - val_loss: 0.2395 - val_mean_absolute_error: 0.2395 - val_mean_absolute_percentage_error: 43.4253
Epoch 100/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.2092 - mean_absolute_error: 0.2092 - mean_absolute_percentage_error: 38.7401 - val_loss: 0.2360 - val_mean_absolute_error: 0.2360 - val_mean_absolute_percentage_error: 43.0443
Epoch 101/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.1820 - mean_absolute_error: 0.1820 - mean_absolute_percentage_error: 34.1212 - val_loss: 0.2293 - val_mean_absolute_error: 0.2293 - val_mean_absolute_percentage_error: 42.0322
Epoch 102/5000
25/25 [==============================] - 0s 2ms/sample - loss: 0.2056 - mean_absolute_error: 0.2056 - mean_absolute_percentage_error: 41.1480 - val_loss: 0.2197 - val_mean_absolute_error: 0.2197 - val_mean_absolute_per

...

Epoch 1050/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0921 - mean_absolute_error: 0.0921 - mean_absolute_percentage_error: 20.0637 - val_loss: 0.1418 - val_mean_absolute_error: 0.1418 - val_mean_absolute_percentage_error: 23.9317
Epoch 1051/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.0960 - mean_absolute_error: 0.0960 - mean_absolute_percentage_error: 21.4311 - val_loss: 0.1454 - val_mean_absolute_error: 0.1454 - val_mean_absolute_percentage_error: 24.8624
Epoch 1052/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0956 - mean_absolute_error: 0.0956 - mean_absolute_percentage_error: 19.2399 - val_loss: 0.1435 - val_mean_absolute_error: 0.1435 - val_mean_absolute_percentage_error: 24.4876
Epoch 1053/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.0908 - mean_absolute_error: 0.0908 - mean_absolute_percentage_error: 21.0177 - val_loss: 0.1409 - val_mean_absolute_error: 0.1409 - val_mean_abs

Epoch 1082/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0992 - mean_absolute_error: 0.0992 - mean_absolute_percentage_error: 19.0315 - val_loss: 0.0966 - val_mean_absolute_error: 0.0966 - val_mean_absolute_percentage_error: 19.4894
Epoch 1083/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.1162 - mean_absolute_error: 0.1162 - mean_absolute_percentage_error: 23.0590 - val_loss: 0.0962 - val_mean_absolute_error: 0.0962 - val_mean_absolute_percentage_error: 19.4885
Epoch 1084/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.1166 - mean_absolute_error: 0.1166 - mean_absolute_percentage_error: 21.4342 - val_loss: 0.1031 - val_mean_absolute_error: 0.1031 - val_mean_absolute_percentage_error: 20.6320
Epoch 1085/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.1193 - mean_absolute_error: 0.1193 - mean_absolute_percentage_error: 24.2833 - val_loss: 0.1061 - val_mean_absolute_error: 0.1061 - val_mean_abs

Epoch 1114/5000
25/25 [==============================] - 0s 19ms/sample - loss: 0.1003 - mean_absolute_error: 0.1003 - mean_absolute_percentage_error: 20.2213 - val_loss: 0.1527 - val_mean_absolute_error: 0.1527 - val_mean_absolute_percentage_error: 32.8638
Epoch 1115/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.1119 - mean_absolute_error: 0.1119 - mean_absolute_percentage_error: 24.7648 - val_loss: 0.1533 - val_mean_absolute_error: 0.1533 - val_mean_absolute_percentage_error: 34.0412
Epoch 1116/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0773 - mean_absolute_error: 0.0773 - mean_absolute_percentage_error: 17.2832 - val_loss: 0.1464 - val_mean_absolute_error: 0.1464 - val_mean_absolute_percentage_error: 32.2220
Epoch 1117/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.1410 - mean_absolute_error: 0.1410 - mean_absolute_percentage_error: 27.6804 - val_loss: 0.1372 - val_mean_absolute_error: 0.1372 - val_mean_abs

Epoch 1177/5000
25/25 [==============================] - 0s 15ms/sample - loss: 0.0812 - mean_absolute_error: 0.0812 - mean_absolute_percentage_error: 16.0630 - val_loss: 0.1034 - val_mean_absolute_error: 0.1034 - val_mean_absolute_percentage_error: 26.9987
Epoch 1178/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0983 - mean_absolute_error: 0.0983 - mean_absolute_percentage_error: 21.7779 - val_loss: 0.1042 - val_mean_absolute_error: 0.1042 - val_mean_absolute_percentage_error: 26.8917
Epoch 1179/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0624 - mean_absolute_error: 0.0624 - mean_absolute_percentage_error: 14.5430 - val_loss: 0.1028 - val_mean_absolute_error: 0.1028 - val_mean_absolute_percentage_error: 26.8011
Epoch 1180/5000
25/25 [==============================] - 0s 16ms/sample - loss: 0.0956 - mean_absolute_error: 0.0956 - mean_absolute_percentage_error: 17.6872 - val_loss: 0.1043 - val_mean_absolute_error: 0.1043 - val_mean_abs

Epoch 1209/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.0732 - mean_absolute_error: 0.0732 - mean_absolute_percentage_error: 14.5743 - val_loss: 0.1024 - val_mean_absolute_error: 0.1024 - val_mean_absolute_percentage_error: 28.9087
Epoch 1210/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.0949 - mean_absolute_error: 0.0949 - mean_absolute_percentage_error: 20.7620 - val_loss: 0.0997 - val_mean_absolute_error: 0.0997 - val_mean_absolute_percentage_error: 27.7708
Epoch 1211/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.1087 - mean_absolute_error: 0.1087 - mean_absolute_percentage_error: 23.5831 - val_loss: 0.1014 - val_mean_absolute_error: 0.1014 - val_mean_absolute_percentage_error: 28.0403
Epoch 1212/5000
25/25 [==============================] - 0s 17ms/sample - loss: 0.0680 - mean_absolute_error: 0.0680 - mean_absolute_percentage_error: 14.8402 - val_loss: 0.1008 - val_mean_absolute_error: 0.1008 - val_mean_abs

In [11]:
#save as excel
#===============

# Define column names for the Excel file
columns = ['Counter', 'lr', 'bs', 'MAE', 'val MAE', 'MAPE', 'val MAPE']
# Convert Results array to a DataFrame
Results_df = pd.DataFrame(Results, columns=columns)
writer = pd.ExcelWriter(path_data_2 + "Results_file_" + str(number_of_test) + ".xlsx", engine='xlsxwriter')
Results_df.to_excel(writer, sheet_name='Results_file_', index=False)
writer.save()

In [12]:
Results_df.head(20)

Counter      lr    bs       MAE   val MAE       MAPE   val MAPE
0         0  0.0100  1000  0.028473  0.125327   5.154047  36.466675
1         1  0.0010  1000  0.047778  0.142339   8.463463  48.740162
2         2  0.0001  1000  0.056988  0.088361  11.725533  22.719419
3         3  0.0100    30  0.029786  0.102677   5.483499  32.018757
4         4  0.0010    30  0.053710  0.121584   9.503659  40.707954
5         5  0.0001    30  0.076670  0.062876  14.795333  18.199362
6         6  0.0100    15  0.040766  0.094736   9.003672  31.296370
7         7  0.0010    15  0.043375  0.086686   8.801979  31.139652
8         8  0.0001    15  0.070986  0.085386  12.854480  32.534435
9         9  0.0100     5  0.068469  0.107153  14.889661  36.951508
10       10  0.0010     5  0.055876  0.112867  10.442715  34.115528
11       11  0.0001     5  0.127393  0.126115  25.901011  30.727921
12       12  0.0100     2  0.081221  0.201192  17.463110  61.238438
13       13  0.0010     2  0.045889  0.106445   8.967632  31.847517
14       14  0.0001     2  0.085834  0.117822  17.505047  28.994947